In [22]:
import pandas as pd
from IPython.display import clear_output, Markdown, Math
import ipywidgets as widgets
import os
import glob
import json
import numpy as np
import itertools
import sklearn.utils as sku
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer, HashingVectorizer
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MultiLabelBinarizer

# simple twitter approach
*for learning emoji usage by single (in the meaning of unconnected) twitter messages*

## loading train data

In [3]:
data_root_folder = "./data_en/" # i created a symlink here

* get all json files in `data_root_folder`

In [4]:
json_files = sorted(glob.glob(data_root_folder + "/*.json"))

----

* so far, only load the first file

In [5]:
twitter_data = pd.read_json(json_files[0])
twitter_data

EMOJI            datetime                  id  \
0                            [🔥, 👏] 2017-11-01 13:29:00  925716304635547600   
1                               [🤦] 2017-11-01 13:29:00  925716304664911900   
2                               [🤧] 2017-11-01 13:29:00  925716304652308500   
3                         [🐯, 🐥, 💕] 2017-11-01 13:29:01  925716308846661600   
4                         [👍, 👍, 👍] 2017-11-01 13:29:02  925716313015586800   
5                               [😒] 2017-11-01 13:29:02  925716313032364000   
6                            [✅, 🍟] 2017-11-01 13:29:02  925716313036722200   
7                               [👶] 2017-11-01 13:29:03  925716317243555800   
8                               [😄] 2017-11-01 13:29:03  925716317214089200   
9                            [🌟, 🌟] 2017-11-01 13:29:03  925716317218508800   
10                              [📷] 2017-11-01 13:29:04  925716321416949800   
11               [🚨, 🚨, 🚨, 🚨, 🚨, 🚨] 2017-11-01 13:29:05  925716325615439900   
12                              [💕] 2017-11-01 13:29:05  925716325615505400   
13                              [🙏] 2017-11-01 13:29:06  925716329797054500   
14                           [😩, 😩] 2017-11-01 13:29:06  925716329801310200   
15                           [😭, 💓] 2017-11-01 13:29:02  925716313019965400   
16                        [🙏, 🤕, 😂] 2017-11-01 13:29:06  925716329801371600   
17                              [😂] 2017-11-01 13:29:05  925716325607133200   
18                              [💯] 2017-11-01 13:29:07  925716334008082400   
19                              [🙄] 2017-11-01 13:29:09  925716342401052700   
20                        [😟, 😥, 😢] 2017-11-01 13:29:10  925716346570240000   
21                        [😂, 😂, 😂] 2017-11-01 13:29:10  925716346603753500   
22                              [👀] 2017-11-01 13:29:10  925716346595434500   
23                              [🔎] 2017-11-01 13:29:11  925716350764331000   
24                           [📣, 💖] 2017-11-01 13:29:12  925716354988236800   
25                           [✨, 💖] 2017-11-01 13:29:12  925716354975465500   
26                              [💪] 2017-11-01 13:29:13  925716359153041400   
27                              [🌻] 2017-11-01 13:29:13  925716359182520300   
28                        [🍁, 🌺, 🍂] 2017-11-01 13:29:15  925716367558545400   
29                              [🍃] 2017-11-01 13:29:16  925716371735900200   
...                             ...                 ...                 ...   
176302                    [😭, 😭, 💘] 2017-11-01 07:23:31  925624327755591700   
176303                 [🤣, 🤣, 🤣, 🤣] 2017-11-01 07:23:33  925624336156938200   
176304                       [😫, ✋] 2017-11-01 07:23:34  925624340342812700   
176305                       [👻, 🎃] 2017-11-01 07:23:34  925624340334501900   
176306                       [😂, 🙁] 2017-11-01 07:23:34  925624340355280900   
176307                          [😭] 2017-11-01 07:23:34  925624340346937300   
176308                       [😢, 💔] 2017-11-01 07:23:34  925624340338507800   
176309                          [🙃] 2017-11-01 07:23:35  925624344524361700   
176310                          [✨] 2017-11-01 07:23:35  925624344511897600   
176311              [😂, 😂, 😂, 😂, 😂] 2017-11-01 07:23:36  925624348710285300   
176312                          [🚀] 2017-11-01 07:23:37  925624352921608200   
176313                    [👌, 👊, 🙌] 2017-11-01 07:23:37  925624352929910800   
176314                          [😴] 2017-11-01 07:23:41  925624369715515400   
176315                       [💀, 🖤] 2017-11-01 07:23:42  925624373905707000   
176316                          [🔴] 2017-11-01 07:23:43  925624378078851100   
176317                 [😂, 😂, 😂, 😂] 2017-11-01 07:23:44  925624382269124600   
176318              [💖, 💗, 💞, 💕, 💘] 2017-11-01 07:23:44  925624382281547800   
176319                          [😀] 2017-11-01 07:23:45  925624386455031800   
176320                          [😎] 2017-11-01 07:23:45  925624386454937600   
1

* extracting emojis and text

In [6]:
emojis = twitter_data['EMOJI']
plain_text = twitter_data['text']

* make our plain text more "plain":
    * removing the keyword `<EMOJI>` (just for the beginning)
    * removing remaining useless emojis, like skin modifier etc.

In [7]:
# defining blacklist for modifier emojis:
emoji_blacklist = set([
    chr(0x1F3FB),
    chr(0x1F3FC),
    chr(0x1F3FD),
    chr(0x1F3FE),
    chr(0x1F3FF),
    chr(0x2642),
    chr(0x2640)
])

In [21]:
# filtering them and the EMOJI keyword out:
plain_text = plain_text.str.replace("<EMOJI>","").str.replace("[" + "".join(list(emoji_blacklist)) + "]","")

In [ ]:
# making a set of the emoji list:



* trying a multi label vectorizer

In [25]:
mlb = MultiLabelBinarizer()

labels = mlb.fit_transform(emojis)

* generating train and test set:

In [30]:
X1, Xt1, y1, yt1 = train_test_split(plain_text, labels, test_size=0.1, random_state=4222)

In [31]:
vectorizer = TfidfVectorizer(stop_words='english')
vec_train = vectorizer.fit_transform(X1)
vec_test = vectorizer.transform(Xt1)

* train. this can take a very long time...

In [40]:
from sklearn.neural_network import MLPClassifier as MLP
from sklearn.multiclass import OneVsRestClassifier as OVRC
from sklearn.tree import DecisionTreeClassifier as DTC

In [49]:
def train():
    clf = OVRC(DTC())

    clf.fit(vec_train[:10000], y1[:10000])
    
    return clf

In [50]:
clf = train()

/home/jonas/.local/lib/python3.6/site-packages/sklearn/multiclass.py:76: UserWarning: Label not 889 is present in all training examples.
  str(classes[c]))
/home/jonas/.local/lib/python3.6/site-packages/sklearn/multiclass.py:76: UserWarning: Label not 897 is present in all training examples.
  str(classes[c]))
/home/jonas/.local/lib/python3.6/site-packages/sklearn/multiclass.py:76: UserWarning: Label not 898 is present in all training examples.
  str(classes[c]))
/home/jonas/.local/lib/python3.6/site-packages/sklearn/multiclass.py:76: UserWarning: Label not 901 is present in all training examples.
  str(classes[c]))
/home/jonas/.local/lib/python3.6/site-packages/sklearn/multiclass.py:76: UserWarning: Label not 902 is present in all training examples.
  str(classes[c]))
/home/jonas/.local/lib/python3.6/site-packages/sklearn/multiclass.py:76: UserWarning: Label not 903 is present in all training examples.
  str(classes[c]))
/home/jonas/.local/lib/python3.6/site-packages/sklearn/multiclas

In [51]:
pred = clf.predict(vectorizer.transform(Xt1))

# build a dataframe to visualize test results:
testlist = pd.DataFrame({'text': Xt1, 'teacher': mlb.inverse_transform(yt1), 'predict': mlb.inverse_transform(pred)})

display(testlist)

predict    teacher  \
57624      (💥, 😡)     (💥, 😡)   
58180          ()       (😒,)   
122719     (😂, 🤦)     (😂, 🤦)   
132425         ()       (🤷,)   
95629        (😂,)       (😂,)   
144805       (😂,)       (🤷,)   
50997      (💕, 🛫)     (💕, 🛫)   
52294          ()     (😍, 😣)   
57600      (⚾, 😬)       (💙,)   
12709        (😂,)       (💀,)   
159921       (😍,)       (👎,)   
1297       (💀, 😂)     (💀, 😂)   
124445         ()       (😩,)   
150159         ()       (🐰,)   
170959     (✅, 🔥)  (✅, 🍋, 🔥)   
46992   (🎬, 💋, 🔗)  (🎬, 💋, 🔗)   
130772       (🎃,)       (🐺,)   
63733          ()       (🎃,)   
22026          ()     (💕, 📷)   
109588     (😍, 😳)       (😍,)   
167358       (🎃,)     (👻, 😈)   
132276         ()       (💀,)   
150897  (😱, 🙈, 🙉)     (🔥, 😈)   
15211        (🎃,)       (🎃,)   
58157      (⌛, 💊)     (⌛, 💊)   
87036        (🔥,)       (😂,)   
68909          ()       (🚗,)   
70063          ()       (😭,)   
53508          ()       (💥,)   
91590        (👀,)       (👀,)   
...           ...        ...   
82637          ()         ()   
151805       (👀,)       (👀,)   
25914          ()       (🔘,)   
91602          ()       (😡,)   
16911          ()       (😩,)   
94798          ()       (🙃,)   
112317       (💪,)       (🤗,)   
72241          ()       (😎,)   
160551     (✨, 💪)       (😭,)   
151889     (👅, 😻)       (😍,)   
64998      (🐶, 💓)     (🐶, 💓)   
138015         ()       (😂,)   
84447          ()       (💕,)   
125899         ()       (🙏,)   
47898        (😂,)       (😂,)   
7597           ()       (😂,)   
173305         ()     (🌈, 💛)   
133827       (💙,)       (💙,)   
157487         ()       (💻,)   
142977     (🌸, 💓)     (🌸, 💓)   
47506        (😭,)     (💙, 🔥)   
164518         ()       (😜,)   
96549      (🐶, 💓)     (🐶, 💓)   
69134          ()     (😞, 😡)   
116753       (💪,)       (🍋,)   
125133       (😑,)     (🖤, 😉)   
5081         (😔,)       (😘,)   
62088          ()       (💔,)   
32769   (😂, 😘, 🙏)       (😁,)   
92385        (😍,)       (💔,)   

                                                     text  
57624    @RealRoseTaylor1: IMO A terrorist doesn’t hav...  
58180    @mog7546: NOT BREAKING NEWS - #KELLY's STUPID...  
122719   @SpecialMonroe: I’m more of like a “ yes nigg...  
132425                      @xo_sweetttnesss Basically ‍️  
95629    @JVino_: Never should of gave niggas technolo...  
144805   @_Erickaaaaaaa: People mad iffy I’m not aroun...  
50997    @MURASAKI_9394: &lt;preview&gt; 171101 ICN@mt...  
52294    @JaDinePhils: Rogue x Gambit x Deadpool No cu...  
57600    @CailenHanzlik: So hyped watching my former t...  
12709   @C_eazyy @RuthlessLuke_ LMAO DED let a nigga s...  
159921  @ShawnHayes_Real @Mr_Ghostly @CR_Shelton @Rojo...  
1297     @Ieansquad: he really solved the equation I c...  
124445  It is really breaking my heart. Imma stick by ...  
150159   @jikookarchive: : aw sexy~: (jimin your cleav...  
170959   @Harrys1DEmpire: 1: Like this2: Follow all th...  
46992    @ONGSEONGWU_TH: [] #WANNAONE X Innisfree | On...  
130772   @lbtreiman: Well i certainly didn't get 'em a...  
63733    @gamngbizzle:  Follow everyone who retweets t...  
22026    @fshion_me: Love it【@perlinek】Coupon code: zo...  
109588                        @SoCuteBabies: Those eyes    
167358   @Lepetit626: Happy Halloween from the cutest ...  
132276                                @marceoooo shuttup   
150897   @instaWANKtube: Drilling babe@mistersex17 @hq...  
15211    @G_Eazy: Hopped out of the millennium falcon ...  
58157    @NBCNewsNight: Stranger Things Neuro Upside D...  
87036   I ran a lot harder back then, as well.I join v...  
68909    @Holy_Boost: SUMMER BOOST case GA!    -Like+ ...  
70063                     I love you so much meliflua ❤️   
53508    @SMMmarkeing786: Get FREE CBD  OIL Trial Bott...  
91590    @dezidoesit: Shea Moisture did not come to pl...  
...                                                   ...  
82637              @KissaSins: Follow me on Instagram!!    
151805   @dezidoesit: Shea Moisture did not c

In [52]:
testlist.to_csv('test.csv')

In [58]:
out = widgets.Output()

t = widgets.Text()
b = widgets.Button(
    description='get smiley',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Click me',
    icon='check'
)



def handle_submit(sender):
    with out:
        clear_output()
    with out:
        display(Markdown("# " + str(mlb.inverse_transform(clf.predict(vectorizer.transform([t.value])))[0])))

b.on_click(handle_submit)
    
display(t)
display(widgets.VBox([b, out]))  

Text(value='')

VBox(children=(Button(description='get smiley', icon='check', style=ButtonStyle(), tooltip='Click me'), Output()))